<!-- WARNING: THIS FILE WAS AUTOGENERATED! DO NOT EDIT! -->

In [ ]:
#| eval: false
load_dotenv()

True

[GPT4 streaming output example on hugging face 🤗](https://huggingface.co/spaces/ysharma/ChatGPT4/blob/main/app.pyhttps://huggingface.co/spaces/ysharma/ChatGPT4/blob/main/app.py)  
[Gradio lite let's you insert Gradio app in browser JS](https://www.gradio.app/guides/gradio-litehttps://www.gradio.app/guides/gradio-lite)  
[Streaming output](https://www.gradio.app/main/guides/streaming-outputshttps://www.gradio.app/main/guides/streaming-outputs)

In [ ]:
#| eval: false
client = OpenAI()
assistant = client.beta.assistants.create(
    name="Vegan Recipe Finder",
    instructions=SYSTEM_PROMPT,
    # + "\nChoose the best single matching recipe to the user's query out of the vegan recipe search returned recipes",
    model="gpt-4o",
    tools=[VEGAN_RECIPE_SEARCH_TOOL_SCHEMA],
)

In [ ]:
class EventHandler(AssistantEventHandler):
    @override
    def on_event(self, event):
        # Retrieve events that are denoted with 'requires_action'
        # since these will have our tool_calls
        if event.event == "thread.run.requires_action":
            run_id = event.data.id  # Retrieve the run ID from the event data
            self.handle_requires_action(event.data, run_id)

    def handle_requires_action(self, data, run_id):
        tool_outputs = []
        for tool_call in data.required_action.submit_tool_outputs.tool_calls:
            if tool_call.function.name == "vegan_recipe_edamam_search":
                fn_args = json.loads(tool_call.function.arguments)
                data = vegan_recipe_edamam_search(
                    query=fn_args.get("query"),
                )
                tool_outputs.append({"tool_call_id": tool_call.id, "output": data})

        self.submit_tool_outputs(tool_outputs, run_id)

    def submit_tool_outputs(self, tool_outputs, run_id):
        client.beta.threads.runs.submit_tool_outputs_stream(
            thread_id=self.current_run.thread_id,
            run_id=self.current_run.id,
            tool_outputs=tool_outputs,
            event_handler=EventHandler(),
        )

In [1]:
#| echo: false
#| output: asis
show_doc(handle_requires_action)

---

[source](https://gitlab.com/animalequality/lv-recipe-chatbot/blob/main/lv_recipe_chatbot/app.py#L22){target="_blank" style="float:right; font-size:smaller"}

### handle_requires_action

>      handle_requires_action (data)

In [ ]:
def run_conversation() -> str:
    run = client.beta.threads.runs.create_and_poll(
        thread_id=thread.id,
        assistant_id=assistant.id,
    )
    while True:
        tool_outputs = []
        tool_calls = (
            []
            if not run.required_action
            else run.required_action.submit_tool_outputs.tool_calls
        )

        for tool_call in tool_calls:
            if tool_call.function.name == "vegan_recipe_edamam_search":
                fn_args = json.loads(tool_call.function.arguments)
                data = vegan_recipe_edamam_search(
                    query=fn_args.get("query"),
                )
                tool_outputs.append({"tool_call_id": tool_call.id, "output": data})

        if tool_outputs:
            try:
                run = client.beta.threads.runs.submit_tool_outputs_and_poll(
                    thread_id=thread.id,
                    run_id=run.id,
                    tool_outputs=tool_outputs,
                )
                print("Tool outputs submitted successfully.")

            except Exception as e:
                print("Failed to submit tool outputs:", e)
                return "Sorry failed to run tools. Try again with a different query."

        if run.status == "completed":
            messages = client.beta.threads.messages.list(thread_id=thread.id)
            data = messages.data
            content = data[0].content
            return content[0].text.value
        time.sleep(0.05)

In [2]:
#| echo: false
#| output: asis
show_doc(run_convo_stream)

---

[source](https://gitlab.com/animalequality/lv-recipe-chatbot/blob/main/lv_recipe_chatbot/app.py#L34){target="_blank" style="float:right; font-size:smaller"}

### run_convo_stream

>      run_convo_stream (thread, content:str, client:openai.OpenAI, assistant)

In [ ]:
thread = client.beta.threads.create()

test_msgs = [
    "Hello",
    "What can I make with tempeh, whole wheat bread, and lettuce?",
]
for m in test_msgs:
    for txt in run_convo_stream(thread, m, client, assistant):
        print(txt, end="")
    print()

skip


In [3]:
#| echo: false
#| output: asis
show_doc(predict)

---

[source](https://gitlab.com/animalequality/lv-recipe-chatbot/blob/main/lv_recipe_chatbot/app.py#L62){target="_blank" style="float:right; font-size:smaller"}

### predict

>      predict (message, history, client:openai.OpenAI, assistant, thread)

In [4]:
#| echo: false
#| output: asis
show_doc(create_demo)

---

[source](https://gitlab.com/animalequality/lv-recipe-chatbot/blob/main/lv_recipe_chatbot/app.py#L102){target="_blank" style="float:right; font-size:smaller"}

### create_demo

>      create_demo (client:openai.OpenAI, assistant)

In [ ]:
if "demo" in globals():
    demo.close()

demo = create_demo(client, assistant)
demo.launch()

skip
